# Your first scraper
In this project, we will guide you step by step through the process of:

1. creating a self-contained development environment.
1. retrieving some information from an API (a website for computers)
2. leveraging it to scrape a website that does not provide an API
3. saving the output for later processing

Here we query an API for a list of countries and their past leaders. We then extract and sanitize their short bio from Wikipedia. Finally, we save the data to disk.

This task is often the first (coding) step of a datascience project and you will often come back to it in the future.

You will study topics such as *scraping*, *data structures*, *regular expressions*, *concurrency* and *file handling*. We will point out useful resources at the appropriate time. 

Let's dive in!

## Creating a clean environment

Use the [`venv`](https://docs.python.org/3/library/venv.html) command to create a new environment called `wikipedia_scraper_env`.

Activate it.

You will find more info about virtual environments in the course content and on the web.

## API Scraping

### A simple API query
You will start with the basics: how to do a simple request to an [API endpoint](../../2.python/2.python_advanced/05.Scraping/5.apis.ipynb).

You will use the [requests](https://requests.readthedocs.io/en/latest/) external library through the `import` keyword.

NOTE: external libraries need to be installed first. Check their documentation.

Check the [Quickstart](https://requests.readthedocs.io/en/latest/user/quickstart/) section of the Requests documentation to:
1. use the `get()` method to connect to this endpoint: https://country-leaders.onrender.com/status
2. check if the `status_code` is equal to 200, which means OK.
    * if OK, `print()` the `text`` of the response.
    * if not, `print()` the `status_code`. 

Here is the signification of [HTTP status codes](https://en.wikipedia.org/wiki/List_of_HTTP_status_codes).


In [1]:
# import the requests library (1 line)
import requests

# assign the root url (without /status) to the root_url variable for ease of reference (1 line)
root_url = "https://country-leaders.onrender.com"

# assign the /status endpoint to another variable called status_url (1 line)
status_url = "https://country-leaders.onrender.com/status"

# query the /status endpoint using the get() method and store it in the req variable (1 line)
req = requests.get(status_url)

# check the status_code using a condition and print appropriate messages (4 lines)
if req.status_code == 200:
    print(req.status_code)
else:
    print(f"Error: {req.status_code}")

200


### Dealing with JSON

[JSON](https://quickref.me/json) is the preferred format to deal with data over the web. You cannot avoid it so you would better get acquainted.

Connect to another endpoint called `/countries` but this time the API will return data in the JSON format. Check what to do in the Requests [Quickstart](https://requests.readthedocs.io/en/latest/user/quickstart/).


In [2]:
# Set the countries_url variable (1 line)
countries_url = "https://country-leaders.onrender.com/countries" 

# query the /countries endpoint using the get() method and store it in the req variable (1 line)
req = requests.get(countries_url)

# Get the JSON content and store it in the countries variable (1 line)
countries = req.json()

# display the request's status code and the countries variable (1 line)
print(f'Status code: {req.status_code}', countries)

Status code: 403 {'message': 'The cookie is missing'}


### Cookies anyone?

It looks like the access to this API is restricted...
Query the `/cookie` endpoint and extract the appropriate field to access your cookie.

You will need to use this cookie in each of the following API requests.

In [3]:
# Set the cookie_url variable (1 line)
cookie_url = "https://country-leaders.onrender.com/cookie"

# Query the enpoint, set the cookies variable and display it (2 lines)
req_cookie = requests.get(cookie_url).cookies
print(req_cookie)

<RequestsCookieJar[<Cookie user_cookie=64c397e0-883b-445b-8ab2-3ab64015c7d3 for country-leaders.onrender.com/>]>


Try to query the countries endpoint using the cookie, save the output and print it.

In [4]:
# query the /countries endpoint, assign the output to the countries variable (1 line)
countries=requests.get(countries_url,cookies=req_cookie)

# display the countries variable (1 line)
print(countries.json())


['us', 'fr', 'ru', 'ma', 'be']


Chances are the cookie has expired... Thanksfully, you got a nice error message. For now, simply execute the last 2 cells quickly so you get a result.

### Getting the actual data from the API

Query the `/leaders` endpoint.

In [5]:
# Set the leaders_url variable (1 line)
leaders_url = "https://country-leaders.onrender.com/leaders"

# query the /leaders endpoint, assign the output to the leaders variable (1 line)
leaders = requests.get(leaders_url).json()

# display the leaders variable (1 line)
print(requests.get(leaders_url, cookies=req_cookie).json())


{'message': 'Please specify a country'}


It looks like this endpoint requires additional information in order to return its result. Check the API [*documentation*](https://country-leaders.onrender.com/docs) in your web browser.

Change the query to accept *parameters*. You should know where to find help by now.

In [6]:
# query the /leaders endpoint using cookies and parameters (take any country in countries)
response_leaders_US = requests.get(leaders_url, cookies = req_cookie, params = "country=us")

# assign the output to the leaders variable (1 line)
leaders_US = response_leaders_US.json()

# display the leaders variable (1 line)
print(leaders_US)

[{'id': 'Q23', 'first_name': 'George', 'last_name': 'Washington', 'birth_date': '1732-02-22', 'death_date': '1799-12-14', 'place_of_birth': 'Westmoreland County', 'wikipedia_url': 'https://en.wikipedia.org/wiki/George_Washington', 'start_mandate': '1789-04-30', 'end_mandate': '1797-03-04'}, {'id': 'Q76', 'first_name': 'Barack', 'last_name': 'Obama', 'birth_date': '1961-08-04', 'death_date': None, 'place_of_birth': 'Kapiolani Medical Center for Women and Children', 'wikipedia_url': 'https://en.wikipedia.org/wiki/Barack_Obama', 'start_mandate': '2009-01-20', 'end_mandate': '2017-01-20'}, {'id': 'Q91', 'first_name': 'Abraham', 'last_name': 'Lincoln', 'birth_date': '1809-02-12', 'death_date': '1865-04-15', 'place_of_birth': 'Sinking Spring Farm', 'wikipedia_url': 'https://en.wikipedia.org/wiki/Abraham_Lincoln', 'start_mandate': '1861-03-04', 'end_mandate': '1865-04-15'}, {'id': 'Q207', 'first_name': 'George', 'last_name': 'Bush', 'birth_date': '1946-07-06', 'death_date': None, 'place_of_bi

### A sneak peak at the data (finally)

Look inside a few examples. Notice the dictionary keys available for each entry. You have your first example of *structured data*. This data was sanitized for your benefit, meaning it is readily exploitable without modification.

You will also notice there is a Wikipedia link for each entry. You will need to extract additional information there. This will be a case of *semi-structured* data.

The /countries endpoint returns a `list` of several country codes.

You need to loop through this list and query the /leaders endpoint for each one. Save each `json` result in a dictionary called `leaders_per_country`.### 数据抢先看（终于）

请看几个示例。注意每个条目的字典键。这就是第一个*结构化数据*示例。为了您的利益，我们对这些数据进行了消毒处理，这意味着无需修改即可利用。

您还会注意到，每个条目都有一个维基百科链接。您需要从这里提取更多信息。这将是一个*半结构化*数据的案例。

/countries 端点会返回一个包含多个国家代码的 "列表"。

您需要循环查看该列表，并针对每个列表查询 /leaders 端点。将每个 `json` 结果保存到名为 `leaders_per_country` 的字典中。

In [7]:
country_codes = ['us', 'fr', 'ru', 'ma', 'be']
leaders_per_country= {}

# 4 lines
for i in country_codes:
    response = requests.get(leaders_url, cookies = req_cookie, params = {'country':i})
    leaders_per_country[i] = response.json()
print(leaders_per_country)

{'us': [{'id': 'Q23', 'first_name': 'George', 'last_name': 'Washington', 'birth_date': '1732-02-22', 'death_date': '1799-12-14', 'place_of_birth': 'Westmoreland County', 'wikipedia_url': 'https://en.wikipedia.org/wiki/George_Washington', 'start_mandate': '1789-04-30', 'end_mandate': '1797-03-04'}, {'id': 'Q76', 'first_name': 'Barack', 'last_name': 'Obama', 'birth_date': '1961-08-04', 'death_date': None, 'place_of_birth': 'Kapiolani Medical Center for Women and Children', 'wikipedia_url': 'https://en.wikipedia.org/wiki/Barack_Obama', 'start_mandate': '2009-01-20', 'end_mandate': '2017-01-20'}, {'id': 'Q91', 'first_name': 'Abraham', 'last_name': 'Lincoln', 'birth_date': '1809-02-12', 'death_date': '1865-04-15', 'place_of_birth': 'Sinking Spring Farm', 'wikipedia_url': 'https://en.wikipedia.org/wiki/Abraham_Lincoln', 'start_mandate': '1861-03-04', 'end_mandate': '1865-04-15'}, {'id': 'Q207', 'first_name': 'George', 'last_name': 'Bush', 'birth_date': '1946-07-06', 'death_date': None, 'plac

In [8]:
# or 1 line
leaders_per_country = {i: requests.get(leaders_url, cookies=req_cookie, params={'country': i}).json() for i in country_codes}
print(leaders_per_country)

{'us': [{'id': 'Q23', 'first_name': 'George', 'last_name': 'Washington', 'birth_date': '1732-02-22', 'death_date': '1799-12-14', 'place_of_birth': 'Westmoreland County', 'wikipedia_url': 'https://en.wikipedia.org/wiki/George_Washington', 'start_mandate': '1789-04-30', 'end_mandate': '1797-03-04'}, {'id': 'Q76', 'first_name': 'Barack', 'last_name': 'Obama', 'birth_date': '1961-08-04', 'death_date': None, 'place_of_birth': 'Kapiolani Medical Center for Women and Children', 'wikipedia_url': 'https://en.wikipedia.org/wiki/Barack_Obama', 'start_mandate': '2009-01-20', 'end_mandate': '2017-01-20'}, {'id': 'Q91', 'first_name': 'Abraham', 'last_name': 'Lincoln', 'birth_date': '1809-02-12', 'death_date': '1865-04-15', 'place_of_birth': 'Sinking Spring Farm', 'wikipedia_url': 'https://en.wikipedia.org/wiki/Abraham_Lincoln', 'start_mandate': '1861-03-04', 'end_mandate': '1865-04-15'}, {'id': 'Q207', 'first_name': 'George', 'last_name': 'Bush', 'birth_date': '1946-07-06', 'death_date': None, 'plac

It is finally time to create a `get_leaders()` function for the above code. You will build on it later-on. This function takes no parameter. Inside it, you will need to:
1. define the urls
2. get the cookies
2. get the countries
3. loop over them and save their leaders in a dictionary
4. return the dictionary

In [9]:
# < 15 lines
def get_leaders():
    # 1. define the urls
    cookie_url = "https://country-leaders.onrender.com/cookie"
    countries_url = "https://country-leaders.onrender.com/countries" 
    leaders_url = "https://country-leaders.onrender.com/leaders"

    # 2. get the cookies
    req_cookie = requests.get(cookie_url).cookies

    # 3. get the countries
    req_countries = requests.get(countries_url, cookies=req_cookie).json()
    
    # 4. loop over them and save their leaders in a dictionary
    leaders_per_country= {}
    for i in country_codes:
        response = requests.get(leaders_url, cookies = req_cookie, params = {'country':i})
        leaders_per_country[i] = response.json()
    return leaders_per_country

Test your function, save the result in the `leaders_per_country` dictionary and check its ouput.

In [10]:
# 2 lines
leaders_per_country = get_leaders()
print(leaders_per_country)

{'us': [{'id': 'Q23', 'first_name': 'George', 'last_name': 'Washington', 'birth_date': '1732-02-22', 'death_date': '1799-12-14', 'place_of_birth': 'Westmoreland County', 'wikipedia_url': 'https://en.wikipedia.org/wiki/George_Washington', 'start_mandate': '1789-04-30', 'end_mandate': '1797-03-04'}, {'id': 'Q76', 'first_name': 'Barack', 'last_name': 'Obama', 'birth_date': '1961-08-04', 'death_date': None, 'place_of_birth': 'Kapiolani Medical Center for Women and Children', 'wikipedia_url': 'https://en.wikipedia.org/wiki/Barack_Obama', 'start_mandate': '2009-01-20', 'end_mandate': '2017-01-20'}, {'id': 'Q91', 'first_name': 'Abraham', 'last_name': 'Lincoln', 'birth_date': '1809-02-12', 'death_date': '1865-04-15', 'place_of_birth': 'Sinking Spring Farm', 'wikipedia_url': 'https://en.wikipedia.org/wiki/Abraham_Lincoln', 'start_mandate': '1861-03-04', 'end_mandate': '1865-04-15'}, {'id': 'Q207', 'first_name': 'George', 'last_name': 'Bush', 'birth_date': '1946-07-06', 'death_date': None, 'plac

## Extracting data from Wikipedia

Query one of the leaders' Wikipedia urls and display its `text` (not JSON).

In [11]:
# 3 lines
nixon = "https://en.wikipedia.org/wiki/Richard_Nixon"
nixon_req = requests.get(nixon)
print(nixon_req.text)

<!DOCTYPE html>
<html class="client-nojs vector-feature-language-in-header-enabled vector-feature-language-in-main-page-header-disabled vector-feature-sticky-header-disabled vector-feature-page-tools-pinned-disabled vector-feature-toc-pinned-clientpref-1 vector-feature-main-menu-pinned-disabled vector-feature-limited-width-clientpref-1 vector-feature-limited-width-content-enabled vector-feature-custom-font-size-clientpref-1 vector-feature-appearance-enabled vector-feature-appearance-pinned-clientpref-1 vector-feature-night-mode-disabled skin-theme-clientpref-day vector-toc-available" lang="en" dir="ltr">
<head>
<meta charset="UTF-8">
<title>Richard Nixon - Wikipedia</title>
<script>(function(){var className="client-js vector-feature-language-in-header-enabled vector-feature-language-in-main-page-header-disabled vector-feature-sticky-header-disabled vector-feature-page-tools-pinned-disabled vector-feature-toc-pinned-clientpref-1 vector-feature-main-menu-pinned-disabled vector-feature-li

Ouch! You get the raw HTML code of the webpage. If you try to deal with it without tools, you will be there all night. Instead, use the [beautiful soup 4](https://www.crummy.com/software/BeautifulSoup/bs4/doc/) *external* library. You will find more info about it [here](../../2.python/2.python_advanced/05.Scraping/1.beautifulsoup_basic.ipynb) and [here](../../2.python/2.python_advanced/05.Scraping/2.beautifulsoup_advanced.ipynb)

Using the Quickstart section, start by importing the library and loading the output of your `get_text()` function.

Use the `prettify()` function and print it to take a look. You will start the actual parsing in the next step.

In [12]:
from bs4 import BeautifulSoup

# 3 lines
response = requests.get("https://en.wikipedia.org/wiki/Joe_Biden")
soup = BeautifulSoup(response.content, 'html.parser')
print(soup.prettify())


<!DOCTYPE html>
<html class="client-nojs vector-feature-language-in-header-enabled vector-feature-language-in-main-page-header-disabled vector-feature-sticky-header-disabled vector-feature-page-tools-pinned-disabled vector-feature-toc-pinned-clientpref-1 vector-feature-main-menu-pinned-disabled vector-feature-limited-width-clientpref-1 vector-feature-limited-width-content-enabled vector-feature-custom-font-size-clientpref-1 vector-feature-appearance-enabled vector-feature-appearance-pinned-clientpref-1 vector-feature-night-mode-disabled skin-theme-clientpref-day vector-toc-available" dir="ltr" lang="en">
 <head>
  <meta charset="utf-8"/>
  <title>
   Joe Biden - Wikipedia
  </title>
  <script>
   (function(){var className="client-js vector-feature-language-in-header-enabled vector-feature-language-in-main-page-header-disabled vector-feature-sticky-header-disabled vector-feature-page-tools-pinned-disabled vector-feature-toc-pinned-clientpref-1 vector-feature-main-menu-pinned-disabled ve

That looks better but you need to extract the right part of the webpage: the text of the first paragraph.

It is a bit tricky because Wikipedia pages slightly differ in structure from one language to the next. We cannot simply get the text for the first HTML paragraph.

You will start by getting all the HTML paragraphs from the HTML source and saving them in the `paragraphs` variable.

Use the documentation or google the appropriate keywords.

In [13]:
import requests
from bs4 import BeautifulSoup
# 2 lines
soup = BeautifulSoup(requests.get("https://en.wikipedia.org/wiki/Joe_Biden").content, 'html.parser')
print('\n'.join([p.get_text() for p in soup.find_all('p')]))




Joseph Robinette Biden Jr.[b] (born November 20, 1942) is an American politician who is the 46th and current president of the United States since 2021. A member of the Democratic Party, he previously served as the 47th vice president from 2009 to 2017 under President Barack Obama and represented Delaware in the United States Senate from 1973 to 2009.

Born in Scranton, Pennsylvania, Biden moved with his family to Delaware in 1953. He graduated from the University of Delaware before earning his law degree from Syracuse University. He was elected to the New Castle County Council in 1970 and to the U.S. Senate in 1972. As a senator, Biden drafted and led the effort to pass the Violent Crime Control and Law Enforcement Act and the Violence Against Women Act. He also oversaw six U.S. Supreme Court confirmation hearings, including the contentious hearings for Robert Bork and Clarence Thomas. Biden ran unsuccessfully for the Democratic presidential nomination in 1988 and 2008. In 2008, Obam

If you try different urls, you might find that the paragraph you want may be at a different index each time.

That is where you need to be clever and ask yourself what would be a reliable way to identify the right index ie. which string matches only the first paragraph whatever the language...

Spend a good 30 minutes on the problem and brainstorm with your fellow learners. If you come out empty handed, ask your coach.

1. Loop over the HTML paragraphs
2. When you have identified the correct one
  * store the [text](https://www.crummy.com/software/BeautifulSoup/bs4/doc/#output) inside the `first_paragraph` variable
  * exit the loop

In [14]:
# <10 lines



At this stage, you can create a function to maintain consistency in your code. We will give you its *skeleton*, you will copy the code you wrote and make it work inside a function.

Don't forget to test your function.

In [1]:
# 10 lines
# def get_first_paragraph(wikipedia_url):
#   print(wikipedia_url) # keep this for the rest of the notebook
#   [insert your code]
#   return first_paragraph

from requests import Session
import re
from bs4 import BeautifulSoup

def get_first_paragraph(wikipedia_url):
    print(wikipedia_url)
    session = Session()
    r = session.get(wikipedia_url)
    soup = BeautifulSoup(r.content, "html.parser")

    paragraphs = soup.select("#mw-content-text > div.mw-parser-output > p")
    
    first_paragraph = ""
    for p in paragraphs:
        text = p.text.strip()
        if len(text.split()) > 20:
            first_paragraph = text
            break
    
    patterns = [
        r"[/][^/]*[/][ ]*[;][ ]*", r"\/.*\/|\[.*\]|\] ;", r"Écouter", r"\(.*Écouter\)", 
        r"Écouter\)", r"Écouter ;", r"\W;", r" ⓘ .*;", r"[A-z-ə]+;", r"uitspraakⓘ ", r"\(uitspraakⓘ\)"
    ]
    for pattern in patterns:
        first_paragraph = re.sub(pattern, "", first_paragraph)
    
    return first_paragraph

In [2]:
# Test: 3 lines
print(get_first_paragraph("https://en.wikipedia.org/wiki/Python_(programming_language)"))
print(get_first_paragraph("https://en.wikipedia.org/wiki/Artificial_intelligence"))
print(get_first_paragraph("https://en.wikipedia.org/wiki/Data_science"))

https://en.wikipedia.org/wiki/Python_(programming_language)
Python is dynamically typed and garbage-collected. It supports multiple programming paradigms, including structured (particularly procedural), object-oriented and functional programming. It is often described as a "batteries included" language due to its comprehensive standard library.
https://en.wikipedia.org/wiki/Artificial_intelligence
Artificial intelligence (AI), in its broadest sense, is intelligence exhibited by machines, particularly computer systems. It is a field of research in computer science that develops and studies methods and software that enable machines to perceive their environment and use learning and intelligence to take actions that maximize their chances of achieving defined goals. Such machines may be called AIs.
https://en.wikipedia.org/wiki/Data_science
Data science is an interdisciplinary academic field


### Regular expressions to the rescue

Now that you have extracted the content of the first paragraph, the only thing that remains to finish your Wikipedia scraper is to sanitize the output.

Indeed some Wikipedia references, HTML code, phonetic pronunciation etc. may linger. You might find *regular expressions* handy to get rid of them and obtain pristine text. You will find some useful documentation about regular expressions [here](../../2.python/2.python_advanced/03.Regex/regex.ipynb)

Once you have one of your regex working online, try it in the cell below. 

Hints: 
* Check the `sub()` method documentation.
* Make sure to test urls in different languages. Some may look good but other do not.

In [17]:
# 3 lines



Overwrite the `get_first_paragraph()` function by applying your regex to the first paragraph before returning it.

In [4]:
# 10 lines
# 10 lines
import requests
from bs4 import BeautifulSoup
import re

def get_first_paragraph(wikipedia_url):
    print(wikipedia_url)  # keep this for the rest of the notebook

    response = requests.get(wikipedia_url)
    soup = BeautifulSoup(response.text, 'html.parser')
    paragraphs = soup.find_all('p')
    
    for paragraph in paragraphs:
        if paragraph.text.strip():
            first_paragraph = paragraph.text.strip()
            break
    
    # Clean up the text using regular expressions
    cleaned_paragraph = re.sub(r'\[.*?\]', '', first_paragraph)  # Remove references
    cleaned_paragraph = re.sub(r'<.*?>', '', cleaned_paragraph)  # Remove HTML tags
    cleaned_paragraph = re.sub(r'\(.+?\)', '', cleaned_paragraph)  # Remove text within parentheses (e.g., pronunciation)

    return cleaned_paragraph

# Test
print(get_first_paragraph("https://en.wikipedia.org/wiki/Web_scraping"))
print(get_first_paragraph("https://en.wikipedia.org/wiki/OpenAI"))
print(get_first_paragraph("https://en.wikipedia.org/wiki/Python_(programming_language)"))


https://en.wikipedia.org/wiki/Web_scraping
Web scraping, web harvesting, or web data extraction is data scraping used for extracting data from websites. Web scraping software may directly access the World Wide Web using the Hypertext Transfer Protocol or a web browser. While web scraping can be done manually by a software user, the term typically refers to automated processes implemented using a bot or web crawler. It is a form of copying in which specific data is gathered and copied from the web, typically into a central local database or spreadsheet, for later retrieval or analysis.
https://en.wikipedia.org/wiki/OpenAI
OpenAI is an American artificial intelligence  research organization founded in December 2015 and headquartered in San Francisco. Its mission is to develop "safe and beneficial" artificial general intelligence, which it defines as "highly autonomous systems that outperform humans at most economically valuable work". As a leading organization in the ongoing AI boom, Ope

Come up with other regexes to capture other patterns and sanitize the outputs completely. Modify your `get_first_paragraph()` function accordingly.

In [3]:
# < 20 lines
import requests
from bs4 import BeautifulSoup
import re

def get_first_paragraph(wikipedia_url):
    print(wikipedia_url)  # keep this for the rest of the notebook

    response = requests.get(wikipedia_url)
    soup = BeautifulSoup(response.text, 'html.parser')
    paragraphs = soup.find('p')
    
    for paragraph in paragraphs:
        if paragraph.text.strip():
            first_paragraph = paragraph.text.strip()
            break
    
    # Clean up the text using regular expressions
    cleaned_paragraph = re.sub(r'\[.*?\]', '', first_paragraph)  # Remove references
    cleaned_paragraph = re.sub(r'<.*?>', '', cleaned_paragraph)  # Remove HTML tags
    cleaned_paragraph = re.sub(r'\(.+?\)', '', cleaned_paragraph)  # Remove text within parentheses (e.g., pronunciation)
    cleaned_paragraph = re.sub(r'\{.*?\}', '', cleaned_paragraph)  # Remove text within braces
    cleaned_paragraph = re.sub(r'&.*?;', '', cleaned_paragraph)  # Remove HTML entities
    cleaned_paragraph = re.sub(r'\s+', ' ', cleaned_paragraph)  # Remove extra whitespace
    
    return cleaned_paragraph

# Test
print(get_first_paragraph("https://en.wikipedia.org/wiki/Web_scraping"))
print(get_first_paragraph("https://en.wikipedia.org/wiki/OpenAI"))
print(get_first_paragraph("https://en.wikipedia.org/wiki/Python_(programming_language)"))

https://en.wikipedia.org/wiki/Web_scraping
Web scraping
https://en.wikipedia.org/wiki/OpenAI


UnboundLocalError: cannot access local variable 'first_paragraph' where it is not associated with a value

## Putting it all together

Let's go back to your `get_leaders()` function and update it with an *inner* loop over each leader. You will query the url provided and extract the first paragraph using the `get_first_paragraph()` function you just finished. You will then update that `leader`'s dictionary and move on to the next one.

Notice, the rest of the code should not change since you modify the leader's data one by one.

In [20]:
# < 20 lines

In [21]:
# Check the output of your function (2 lines)


Does the function crash in the middle of the loop? Chances are the cookies have expired while looping over the leaders.

Modify your function with an *exception* or check if the `status_code` is a cookie error. In either case, get new cookies and query the api again.

If your code did not crash,

In [22]:
# < 25 lines



Check the output of your function again.

In [23]:
# Check the output of your function (1 line)


Well done! It took a while however... Let's speed things up. The main *bottleneck* is the loop. We call on the Wikipedia website many times.

You will use the same *session* to call all the wikipedia pages. Check the *Advanced Usage* section of the Requests module's documentation.

Start by modifying the `get_first_paragraph()` function to accept a session parameter and adjust the `get()` method call.

In [24]:
# < 20 lines


Modify your `get_leaders()` function to make use of a single session for all the Wikipedia calls.
1. create a `Session` object outside of the loop over countries.
2. pass it to the `get_first_paragraph()` function as an argument.

In [25]:
# <25 lines


Test your new functions.



## Saving your hard work

The final step is to save the ``leaders_per_country`` dictionary in the `leaders.json` file using the [json](https://docs.python.org/3/library/json.html) module. Check out the `with` statement.

In [26]:
# 3 lines


Make sure the file can be read back. Write the code to read the file. And check the variables are the same.

In [27]:
# 3 lines


Make a function `save(leaders_per_country)` to call this code easily.

In [28]:
# 3 lines


In [29]:
# Call the function (1 line)


## Tidy things up in a stand-alone python script

Congratulations! You now have a working scraper! However, your code is scattered throughout this notebook along side the tutorials. Hardly production ready...

Copy and paste what you need in a separate `leaders_scraper.py` file.
Make sure it works by calling `python3 leaders_scraper.py`

## To go further

If you want to practice scraping, you can read this section and tackle the exercise.

You have noticed the API returns very partial results for country leaders. Many are missing. Overwrite the `get_leaders()` function to get its list from Wikipedia and extract their *personal details* from the frame on the side.

Good luck!

In [8]:
#scraper.py
import json
import re
import requests
from requests import Session
from bs4 import BeautifulSoup

class WikipediaScraper:
    def __init__(self, base_url:str="https://country-leaders.onrender.com"):
        self.base_url= base_url
        self.country_endpoint = base_url+"/countries"
        self.leaders_endpoint = base_url+"/leaders"
        self.cookies_endpoint = base_url+"/cookie"
        self.leaders_data = {}
        self.cookie = requests.get(self.cookies_endpoint).cookies

    def __str__(self):
        return f"WikipediaScraper requests the {self.base_url} API to get data about the leaders of the countries in the list."

    def refresh_cookie(self) -> object:
        return requests.get(self.cookies_endpoint).cookies

    def get_countries(self) -> list:
        return requests.get(self.country_endpoint, cookies=self.cookie).json()

    def get_first_paragraph(self, wikipedia_url: str, session = Session()) -> str:
        r = session.get(wikipedia_url)
        soup = BeautifulSoup(r.content, "html.parser")
        paragraphs =  soup.select("#mw-content-text > div.mw-parser-output > p")
        paragraphs = [p for p in paragraphs if len(p.text.strip())>0]
        first_paragraph = paragraphs[0].text
        patterns = [r"[/][^/]*[/][ ]*[;][ ]*", r"\/.*\/|\[.*\]|\] ;", r"Écouter", r"\(.*Écouter\)", r"Écouter\)", r"Écouter ;", r"\W;", r" ⓘ .*;", r"[A-z-ə]+;", r"uitspraakⓘ ", r"\(uitspraakⓘ\)"]
        for pattern in patterns:
            first_paragraph = re.sub(pattern, "", first_paragraph)
        return first_paragraph

    def get_leaders(self, country: str) -> None:
        session = Session()
        params = {"country":f"{country}"}
        self.leaders_data[country] = session.get(self.leaders_endpoint, cookies=self.refresh_cookie(), params=params).json()
        for i in range(len(self.leaders_data[country])):
            self.leaders_data[country][i]["first_paragraph"] = self.get_first_paragraph(self.leaders_data[country][i]["wikipedia_url"], session)
        
    def to_json_file(self, filepath: str) -> None:
        with open (filepath, "w", encoding="utf-8") as f:
            json.dump(self.leaders_data, f, indent=4, ensure_ascii = False)

In [9]:
#main.py
from scraper import WikipediaScraper
from tqdm import tqdm

print("Scraping the data...")

object = WikipediaScraper()

for country in tqdm(object.get_countries()):
    object.get_leaders(country)

print("Saving the data...")

object.to_json_file("leaders_data.json")

print("Done!")

ModuleNotFoundError: No module named 'scraper'